# CNN-LSTM

In [ ]:
%

In [1]:
import pandas as pd
import numpy as np
from tqdm import tqdm
from keras.models import Sequential
from keras.layers import Dense, LSTM, Conv1D, MaxPooling1D, Flatten
from keras.callbacks import EarlyStopping
from keras.preprocessing.sequence import TimeseriesGenerator
from sklearn.preprocessing import MinMaxScaler

C:\Users\asaf0\anaconda3\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
train = pd.read_csv('./train.csv')

In [3]:
# 추론 결과를 저장하기 위한 dataframe 생성
results_df = pd.DataFrame(columns=['종목코드', 'final_return'])

In [4]:
# train 데이터에 존재하는 독립적인 종목코드 추출
unique_codes = train['종목코드'].unique()

In [5]:
# 각 종목코드에 대해서 모델 학습 및 추론 반복
for code in tqdm(unique_codes):
    
    # 학습 데이터 생성
    train_close = train[train['종목코드'] == code][['일자', '종가']]
    train_close['일자'] = pd.to_datetime(train_close['일자'], format='%Y%m%d')
    train_close.set_index('일자', inplace=True)
    tc = train_close['종가'].values.reshape(-1, 1)
    
    # 데이터 정규화
    scaler = MinMaxScaler()
    tc = scaler.fit_transform(tc)
    
    # 시퀀스 데이터 생성
    n_input = 30  # lookback window
    n_features = 1  # number of features
    generator = TimeseriesGenerator(tc, tc, length=n_input, batch_size=8)

    # CNN-LSTM 모델 구성
    model = Sequential()
    model.add(Conv1D(filters=64, kernel_size=3, activation='relu', input_shape=(n_input, n_features)))
    model.add(MaxPooling1D(pool_size=2))
    model.add(LSTM(50, activation='relu'))
    model.add(Dense(1))
    model.compile(optimizer='adam', loss='mse')

    # Early stopping 콜백 선언
    es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=10)
    
    # 모델 학습
    model.fit(generator, epochs=15, verbose=0, callbacks=[es])
    
    # 향후 15일 동안의 예측 생성
    pred_list = []
    batch = tc[-n_input:].reshape((1, n_input, n_features))

    for i in range(n_input):   
        pred_list.append(model.predict(batch)[0]) 
        batch = np.append(batch[:,1:,:],[[pred_list[i]]],axis=1)

    # 최종 수익률 계산
    final_return = (scaler.inverse_transform(pred_list)[-1] - scaler.inverse_transform(pred_list)[0]) / scaler.inverse_transform(pred_list)[0]
    
    # 결과 저장
    results_df = results_df.append({'종목코드': code, 'final_return': final_return[0]}, ignore_index=True)

  0%|                                                                                         | 0/2000 [00:00<?, ?it/s]

1/1 [==============================] - 0s 15ms/step


  0%|                                                                               | 1/2000 [00:05<3:01:42,  5.45s/it]

1/1 [==============================] - 0s 14ms/step


  0%|                                                                               | 2/2000 [00:10<2:59:18,  5.38s/it]

...

100%|██████████████████████████████████████████████████████████████████████████▉| 1998/2000 [12:13:47<02:19, 69.91s/it]

1/1 [==============================] - 0s 41ms/step


100%|██████████████████████████████████████████████████████████████████████████▉| 1999/2000 [12:14:55<01:09, 69.21s/it]

1/1 [==============================] - 0s 40ms/step


100%|███████████████████████████████████████████████████████████████████████████| 2000/2000 [12:16:03<00:00, 22.08s/it]


In [1]:
results_df['순위'] = results_df['final_return'].rank(method='first', ascending=False).astype('int') # 각 순위를 중복없이 생성
results_df

NameError: name 'results_df' is not defined

In [7]:
sample_submission = pd.read_csv('./sample_submission.csv')
sample_submission

종목코드    순위
0     A000020     1
1     A000040     2
2     A000050     3
3     A000070     4
4     A000080     5
...       ...   ...
1995  A375500  1996
1996  A378850  1997
1997  A383220  1998
1998  A383310  1999
1999  A383800  2000

[2000 rows x 2 columns]

In [8]:
baseline_submission = sample_submission[['종목코드']].merge(results_df[['종목코드', '순위']], on='종목코드', how='left')
baseline_submission

종목코드    순위
0     A000020   822
1     A000040  1387
2     A000050   843
3     A000070  1359
4     A000080  1276
...       ...   ...
1995  A375500   378
1996  A378850   973
1997  A383220   370
1998  A383310  1760
1999  A383800   772

[2000 rows x 2 columns]

In [2]:
baseline_submission.to_csv('cnn_lstm_submission.csv', index=False)

NameError: name 'baseline_submission' is not defined